# Skew-T's
## Requesting Upper Air Data from Siphon and Plotting a Skew-T with MetPy
### Based on <a href = "http://www.unidata.ucar.edu"> Unidata's </a> <i> MetPy Monday </i> \# 15 -17 YouTube links: <br>https://www.youtube.com/watch?v=OUTBiXEuDIU; <br> https://www.youtube.com/watch?v=oog6_b-844Q; <br> https://www.youtube.com/watch?v=b0RsN9mCY5k

### Import the libraries we need

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.gridspec as gridspec
from mpl_toolkits.axes_grid1.inset_locator import inset_axes
import metpy.calc as mpcalc
from metpy.plots import Hodograph, SkewT
from metpy.units import units, pandas_dataframe_to_unit_arrays
from datetime import datetime, timedelta
import pandas as pd
from siphon.simplewebservice.wyoming import WyomingUpperAir

### Next we use methods from the datetime library to determine the latest time, and then use it to select the most recent date and time that we'll use for our selected Skew-T.

In [ ]:
now = datetime.now()

curr_year = now.year
curr_month = now.month
curr_day = now.day
curr_hour = now.hour

print(f"Current time is: {now}")
print(f"Current year, month, date, hour: {curr_year}, {curr_month}, {curr_day}, {curr_hour}")

if (curr_hour > 13) :
    raob_hour = 12
    hr_delta = curr_hour - 12
elif (curr_hour > 1):
    raob_hour = 0
    hr_delta = curr_hour - 0
else:
    raob_hour = 12
    hr_delta = curr_hour + 12

raob_time = now - timedelta(hours=hr_delta)

raob_year = raob_time.year
raob_month = raob_time.month
raob_day = raob_time.day
raob_hour = raob_time.hour

print(f"Time of RAOB is: {raob_year}, {raob_month}, {raob_day}, {raob_hour}")



### Construct a datetime object that we will use in our query to the data server. Note what it looks like.

In [ ]:
query_date = datetime(raob_year,raob_month,raob_day,raob_hour)
query_date

### If desired, we can choose a past date and time.

In [ ]:
#current = True
current = False

In [ ]:
if (current == False):
    query_date = datetime(2025, 4, 2, 18)
    
raob_timeStr = query_date.strftime("%Y-%m-%d %H UTC")
raob_timeTitle = query_date.strftime("%H00 UTC %-d %b %Y")
print(raob_timeStr)
print(raob_timeTitle)

### Select our station and query the data server.

In [ ]:
station = 'ILX'

df = WyomingUpperAir.request_data (query_date,station)

<div class="alert alert-warning">
    <b>Possible data retrieval errors:</b>
    <ul>
        <li>If you get a <code>No data available for YYYY-MM-DD HHZ for station XXX </code>, you may have specified an incorrect date or location, or there just might not have been a successful RAOB at that date and time.</code></li>
        <li>If you get a <code>503 Server Error</code>, try requesting the sounding again. The Wyoming server does not handle simultaneous requests well. Usually the request will eventually work. </li>
    </ul>
    
</div>

### What does the returned data file look like? Well, it looks like a Pandas Dataframe!

In [ ]:
df

Examine one of the columns

In [ ]:
df['pressure']

### The University of Wyoming sounding reader includes a <i>units</i> attribute, which produces a Python dictionary of units specific to Wyoming sounding data.  What does it look like? 

In [ ]:
df.units

### Attach units to the various columns using MetPy's `pandas_dataframe_to_unit_arrays` function, as follows:

In [ ]:
df = pandas_dataframe_to_unit_arrays(df)

Now that units are attached, how does the `pressure` column look?

In [ ]:
df['pressure']

### As with any Pandas Dataframe, we can select columns, so we do so now for all the relevant variables for our Skew-T. 

In [ ]:
P = df['pressure']
Z = df['height']
T = df['temperature']
Td = df['dewpoint']
u = df['u_wind']
v = df['v_wind']

Now that `u` and `v` are *units aware*, we can use one of MetPy's diagnostic routines to calculate the wind speed from the vector's components.

In [ ]:
wind_speed = mpcalc.wind_speed(u,v)

In [ ]:
wind_speed

Thermodynamic Calculations
--------------------------

Often times we will want to calculate some thermodynamic parameters of a
sounding. The MetPy calc module has many such calculations already implemented!

* **Lifting Condensation Level (LCL)** - The level at which an air parcel's
  relative humidity becomes 100% when lifted along a dry adiabatic path.
* **Parcel Path** - Path followed by a hypothetical parcel of air, beginning
  at the surface temperature/pressure and rising dry adiabatically until
  reaching the LCL, then rising moist adiabatially.

### Calculate the LCL. Note that the units will appear at the end when we print them out!

In [ ]:
lclp, lclt = mpcalc.lcl(P[0], T[0], Td[0])
print (f'LCL Pressure = ,{lclp}, LCL Temperature = ,{lclt}')

### Calculate the parcel profile. Here, we pass in the array of all pressure values, and specify the first (index 0, remember Python's zero-based indexing) index of the temperature and dewpoint arrays as the starting point of the parcel path.

In [ ]:
parcel_prof = mpcalc.parcel_profile(P, T[0], Td[0])

### What does the parcel profile look like? Well, it's just an array of all the temperatures of the parcel at each of the pressure levels as it ascends.

In [ ]:
parcel_prof

### Set the limits for the x- and y-axes so they can be changed and easily re-used when desired.

In [ ]:
pTop = 100
pBot = 1050
tMin = -60
tMax = 40

### Since we are plotting a skew-T, define the log-p axis.

In [ ]:
logTop = np.log10(pTop)
logBot = np.log10(pBot)
interval = np.logspace(logTop,logBot) * units('hPa')

### This interval will tend to oversample points near the top of the atmosphere relative to the bottom. One effect of this will be that wind barbs will be hard to read, especially at higher levels. Use a resampling method from NumPy to deal with this.

In [ ]:
idx = mpcalc.resample_nn_1d(P, interval)

### Now we are ready to create our skew-T. Plot it and save it as a PNG file.

<div class="alert alert-warning">
    <b>Note:</b>
    Annoyingly, when specifying the color of the dry/moist adiabats, and mixing ratio lines, the parameter must be <b>color<i>s</i></b>, not <b>color</b>. In other Matplotlib-related code lines in the cell below where we set the color, such as <code>skew.ax.axvline</code> ,<b> color</b> must be singular.<br><br>
    <p> Additionally, some of the skew-T attributes (e.g. the shaded area between -12 and -18 C) may not be relevant (e.g., a warm-season convective case). Comment out those you don't wish to show.</p>
</div>

In [ ]:
# Create a new figure. The dimensions here give a good aspect ratio
fig = plt.figure(figsize=(9, 9))
skew = SkewT(fig, rotation=45)

# Plot the data using normal plotting functions, in this case using
# log scaling in Y, as dictated by the typical meteorological plot
skew.plot(P, T, 'r', linewidth=3)
skew.plot(P, Td, 'g', linewidth=3)
skew.plot_barbs(P[idx], u[idx], v[idx])
skew.ax.set_ylim(pBot, pTop)
skew.ax.set_xlim(tMin, tMax)

# Plot LCL as black dot
skew.plot(lclp, lclt, 'ko', markerfacecolor='black')

# Plot the parcel profile as a black line
skew.plot(P, parcel_prof, 'k', linestyle='--', linewidth=2)

# Shade areas of CAPE and CIN
skew.shade_cin(P, T, parcel_prof)
skew.shade_cape(P, T, parcel_prof)

# Shade areas between a certain temperature (in this case, the DGZ)
#skew.shade_area(P.m,-18,-12,color=['purple'])
# Plot a zero degree isotherm
skew.ax.axvline(0, color='c', linestyle='-', linewidth=2)

# Add the relevant special lines
skew.plot_dry_adiabats()
skew.plot_moist_adiabats(colors='#58a358', linestyle='-')
skew.plot_mixing_lines()

plt.title(f"RAOB for {station} valid at: {raob_timeTitle}")
# Create a hodograph
# Create an inset axes object that is 30% width and height of the
# figure and put it in the upper right hand corner.
ax_hod = inset_axes(skew.ax, '30%', '30%', loc=1)
h = Hodograph(ax_hod, component_range=100.)
h.add_grid(increment=30)
h.plot_colormapped(u, v, df['height'])
plt.savefig (f"{station}_{raob_timeStr}_skewt.png")

Here's how the plot would appear if we hadn't done the resampling. Note that the wind barbs are plotted at every level, and are harder to read:

In [ ]:
# Create a new figure. The dimensions here give a good aspect ratio
fig = plt.figure(figsize=(9, 9))
skew = SkewT(fig, rotation=45)

# Plot the data using normal plotting functions, in this case using
# log scaling in Y, as dictated by the typical meteorological plot
skew.plot(P, T, 'r', linewidth=3)
skew.plot(P, Td, 'g', linewidth=3)
skew.plot_barbs(P, u, v)
skew.ax.set_ylim(pBot, pTop)
skew.ax.set_xlim(tMin, tMax)

# Plot LCL as black dot
skew.plot(lclp, lclt, 'ko', markerfacecolor='black')

# Plot the parcel profile as a black line
skew.plot(P, parcel_prof, 'k', linestyle='--', linewidth=2)

# Shade areas of CAPE and CIN
skew.shade_cin(P, T, parcel_prof)
skew.shade_cape(P, T, parcel_prof)

# Shade areas between a certain temperature (in this case, the DGZ)
#skew.shade_area(P.m,-18,-12,color=['purple'])
# Plot a zero degree isotherm
skew.ax.axvline(0, color='c', linestyle='-', linewidth=2)

# Add the relevant special lines
skew.plot_dry_adiabats()
skew.plot_moist_adiabats(colors='#58a358', linestyle='-')
skew.plot_mixing_lines()

plt.title(f"RAOB for {station} valid at: {raob_timeTitle}")

# Create a hodograph
# Create an inset axes object that is 30% width and height of the
# figure and put it in the upper right hand corner.
ax_hod = inset_axes(skew.ax, '30%', '30%', loc=1)
h = Hodograph(ax_hod, component_range=100.)
h.add_grid(increment=30)
h.plot_colormapped(u, v, df['height'])  # Plot a line colored by a parameter

<div class="alert alert-success">
    <b>What's next:</b>
    Try different RAOB locations and dates (for example, draw a skew-t relevant to your class project). <br>
    Here is a link to <a href="https://www.weather.gov/upperair/nws_upper">a map of NWS RAOB sites</a>.<br>
    Depending on the situation, you may want to omit plotting the DGZ, LCL, parcel path, CAPE/CIN, freezing line, and/or move the location of the hodograph.<br>
</div>